# Optimize Initial Conditions
## Yabox

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Initialize Ray

In [2]:
from environs import Env
env = Env()
env.str("CUDA_DEVICE_ORDER",'PCI_BUS_ID')
env.str("CUDA_VISIBLE_DEVICES","96")
env.int("NUMBA_ENABLE_CUDASIM",1)
env.bool("OMPI_MCA_opal_cuda_support",True)

import os
import ray
MB=1024*1024
GB=MB*1024
ray.shutdown()
ray.init(num_gpus=96,num_cpus=17,
         ignore_reinit_error=True)

@ray.remote(num_gpus=1)
def use_gpu():
    print("ray.get_gpu_ids(): {}".format(ray.get_gpu_ids()[0]))
    print("CUDA_VISIBLE_DEVICES: {}".format(os.environ["CUDA_VISIBLE_DEVICES"]))

use_gpu.remote()

2021-03-02 10:22:08,754	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8265


ObjectRef(df5a1a828c9685d3ffffffff0100000001000000)

# Load New and Process Data from website data.brasil.io

In [3]:
%reload_ext autoreload
%autoreload 2
import get_data as gd
LoadData=False

if LoadData:
    gd.get_data()

# Functions to Load Processed Data

In [4]:
def load_confirmed(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    start=datetime.strptime(start_date, "%Y-%m-%d")+timedelta(days=40)
    start2=start.strftime("%Y-%m-%d")
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2 =df2.apply (pd.to_numeric, errors='coerce')
    df2[start2:] = df2[start2:].replace({0:np.nan})
    df2 = df2.dropna()
    df2.index = pd.DatetimeIndex(df2.index)
    #interpolate missing data
    df2 = df2.reindex(pd.date_range(df2.index.min(), df2.index.max()), fill_value=np.nan)
    df2 = df2.interpolate(method='akima', axis=0).ffill().bfill()
    #string type for dates and integer for data
    df2 = df2.astype(int)
    df2.index = df2.index.astype(str)
    #select dates
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(districtRegion, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/DRS_mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    start=datetime.strptime(start_date, "%Y-%m-%d")+timedelta(days=40)
    start2=start.strftime("%Y-%m-%d")
    for i in range(0,len(df.date)):
        y.append(df[districtRegion].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2 =df2.apply (pd.to_numeric, errors='coerce')
    df2[start2:] = df2[start2:].replace({0:np.nan})
    df2 = df2.dropna()
    df2.index = pd.DatetimeIndex(df2.index)
    #interpolate missing data
    df2 = df2.reindex(pd.date_range(df2.index.min(), df2.index.max()), fill_value=np.nan)
    df2 = df2.interpolate(method='akima', axis=0).ffill().bfill()
    #string type for dates and integer for data
    df2 = df2.astype(int)
    df2.index = df2.index.astype(str)
    #select dates
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Load solver

In [5]:
import LearnerICRayNoLoadBHNewModel_v4 as L 

# Data for Regions

In [6]:
dfparam = pd.read_csv("data/param.csv")
dfPopEst = pd.read_csv("data/DRS_popEst.csv")
dfparam['popEst']=dfPopEst.popEst
dfparam['RATIO']=0
display(dfparam)


DRS  start-date  prediction-range         s0  \
0        DRS 01 - Grande São Paulo  2020-03-20               200  2000000.0   
1               DRS 02 - Araçatuba  2020-04-01               200      500.0   
2              DRS 03 - Araraquara  2020-04-01               200     2000.0   
3        DRS 04 - Baixada Santista  2020-04-01               200     8000.0   
4                DRS 05 - Barretos  2020-04-01               200     2000.0   
5                   DRS 06 - Bauru  2020-04-01               200    10000.0   
6                DRS 07 - Campinas  2020-04-01               200    20000.0   
7                  DRS 08 - Franca  2020-04-01               200     1000.0   
8                 DRS 09 - Marília  2020-04-01               200     5000.0   
9              DRS 10 - Piracicaba  2020-04-01               200    10000.0   
10    DRS 11 - Presidente Prudente  2020-04-01               200     1000.0   
11               DRS 12 - Registro  2020-04-01               200     1000.0   
12         DRS 13 - Ribeirão Preto  2020-04-01               200     5000.0   
13  DRS 14 - São João da Boa Vista  2020-04-01               200     2000.0   
14  DRS 15 - São José do Rio Preto  2020-04-01               200    10000.0   
15               DRS 16 - Sorocaba  2020-04-01               200     1200.0   
16                DRS 17 - Taubaté  2020-04-01               200    10000.0   

        e0      a0        i0        r0        d0  START  RATIO  WCASES  WREC  \
0   0.0001  0.0001  800.0000  300.0000  400.0000      0      0    0.15  0.05   
1   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
2   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
3   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
4   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
5   0.0001  0.0001    4.0000    0.0001    0.0001      0      0    0.40  0.10   
6   0.0001  0.0001   40.0000    0.0001    0.0001      0      0    0.40  0.10   
7   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
8   0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
9   0.0001  0.0001    0.0001    0.0001    1.0000      0      0    0.40  0.10   
10  0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
11  0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
12  0.0001  0.0001    0.0001    0.0001    0.0001      5      0    0.40  0.10   
13  0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
14  0.0001  0.0001    0.0001    0.0001    0.0001      0      0    0.40  0.10   
15  0.0001  0.0001    2.0000    0.0001    0.0001      0      0    0.40  0.10   
16  0.0001  0.0001   17.0000    0.0001    2.0000      0      0    0.40  0.10   

        popEst  
0   21734682.0  
1     791256.0  
2    1025982.0  
3    1865397.0  
4     440907.0  
5    1800757.0  
6    4671287.0  
7     718176.0  
8    1149132.0  
9    1586546.0  
10    775627.0  
11    284509.0  
12   1523682.0  
13    834872.0  
14   1629470.0  
15   2534157.0  
16   2552610.0

In [7]:
dfSP = pd.read_csv("data/dados_municipios_SP.csv")

# lista DRSs
DRS = list(dfSP["DRS"].unique())
DRS.remove("Indefinido")

dfSP

date state   city place_type  confirmed  deaths  \
0       2021-02-01    SP  TOTAL      state    1779722   53090   
1       2021-01-31    SP  TOTAL      state    1777368   53034   
2       2021-01-30    SP  TOTAL      state    1773024   52954   
3       2021-01-29    SP  TOTAL      state    1759957   52722   
4       2021-01-28    SP  TOTAL      state    1746070   52481   
...            ...   ...    ...        ...        ...     ...   
155027  2020-06-23    SP   Óleo       city          1       0   
155028  2020-06-22    SP   Óleo       city          1       0   
155029  2020-06-21    SP   Óleo       city          1       0   
155030  2020-06-20    SP   Óleo       city          1       0   
155031  2020-06-19    SP   Óleo       city          1       0   

        order_for_place  is_last      popEst  estimated_population  \
0                   336     True  45919049.0            46289333.0   
1                   335    False  45919049.0            46289333.0   
2                   334    False  45919049.0            46289333.0   
3                   333    False  45919049.0            46289333.0   
4                   332    False  45919049.0            46289333.0   
...                 ...      ...         ...                   ...   
155027                5    False      2496.0                2471.0   
155028                4    False      2496.0                2471.0   
155029                3    False      2496.0                2471.0   
155030                2    False      2496.0                2471.0   
155031                1    False      2496.0                2471.0   

        city_ibge_code  confirmed_per_100k_inhabitants  death_rate  \
0                 35.0                      3844.77780      0.0298   
1                 35.0                      3839.69240      0.0298   
2                 35.0                      3830.30795      0.0299   
3                 35.0                      3802.07898      0.0300   
4                 35.0                      3772.07855      0.0301   
...                ...                             ...         ...   
155027       3533809.0                        40.46945      0.0000   
155028       3533809.0                        40.46945      0.0000   
155029       3533809.0                        40.46945      0.0000   
155030       3533809.0                        40.46945      0.0000   
155031       3533809.0                        40.46945      0.0000   

                     DRS  
0             Indefinido  
1             Indefinido  
2             Indefinido  
3             Indefinido  
4             Indefinido  
...                  ...  
155027  DRS 09 - Marília  
155028  DRS 09 - Marília  
155029  DRS 09 - Marília  
155030  DRS 09 - Marília  
155031  DRS 09 - Marília  

[155032 rows x 14 columns]

# Functions for Optimization

In [8]:
from scipy.integrate import odeint
import sys
import io
import gc

def create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version):
                
    def fobjective(point):
        
        cleanRecovered=False
        s0, deltaDate, i0, d0, startNCases, weigthCases = point
        weigthRecov=0
        ratio=0
        dead = load_dead(districtRegion,date)
        data = load_confirmed(districtRegion,date)*(1-ratio)-dead
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=deltaDate)
        f=L.Learner.remote(districtRegion, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, point,f         

        gc.collect()

        return result
    return fobjective

In [9]:
@ray.remote(num_cpus=0,num_gpus=4) #, max_calls=1)
def opt(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, 
        ratio, predict_range, popEst, version):

    bounds=[(0.3*popEst,0.99*popEst),(-4,4),(0,250), (0,250), (0,250),\
              (0.19,0.85)]
    maxiterations=500
    runDate=datetime.today()
    f=create_f(districtRegion,e0,a0,r0,date, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    
    return p

# Main Code

In [10]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines){
    return true;}

<IPython.core.display.Javascript object>

In [11]:
DRS=dfparam.DRS
display(DRS)
version="119"
gc.enable()

optimal=[]
for districtRegion in DRS:
    #remove previous history file
    strFile='./results/history_'+districtRegion+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec,popEst = parameters
    optimal.append(opt.remote(districtRegion,s0,i0,e0,a0,r0,d0,wcases,date,startNCases, \
                              ratio, predict_range, popEst, version))        
    

0          DRS 01 - Grande São Paulo
1                 DRS 02 - Araçatuba
2                DRS 03 - Araraquara
3          DRS 04 - Baixada Santista
4                  DRS 05 - Barretos
5                     DRS 06 - Bauru
6                  DRS 07 - Campinas
7                    DRS 08 - Franca
8                   DRS 09 - Marília
9                DRS 10 - Piracicaba
10      DRS 11 - Presidente Prudente
11                 DRS 12 - Registro
12           DRS 13 - Ribeirão Preto
13    DRS 14 - São João da Boa Vista
14    DRS 15 - São José do Rio Preto
15                 DRS 16 - Sorocaba
16                  DRS 17 - Taubaté
Name: DRS, dtype: object

In [ ]:
optimal=ray.get(optimal)

(pid=18405) basinhopping step 0: f 1.28019e+08
(pid=18403) basinhopping step 0: f 2.37903e+09
(pid=18403) basinhopping step 1: f 2.37903e+09 trial_f 2.41671e+09 accepted 0  lowest_f 2.37903e+09
(pid=18401) basinhopping step 0: f 1.63164e+09
(pid=18405) basinhopping step 1: f 1.28019e+08 trial_f 1.29378e+08 accepted 0  lowest_f 1.28019e+08
(pid=18401) warning: basinhopping: local minimization failure
(pid=18401) basinhopping step 1: f 1.63164e+09 trial_f 2.83323e+10 accepted 0  lowest_f 1.63164e+09
(pid=18402) warning: basinhopping: local minimization failure
(pid=18402) basinhopping step 0: f 1.44227e+08
(pid=18405) warning: basinhopping: local minimization failure
(pid=18405) basinhopping step 2: f 1.28019e+08 trial_f 1.30032e+08 accepted 0  lowest_f 1.28019e+08
(pid=18406) basinhopping step 0: f 1.83413e+08
(pid=18405) basinhopping step 3: f 1.28019e+08 trial_f 1.28131e+08 accepted 0  lowest_f 1.28019e+08
(pid=18401) basinhopping step 2: f 1.59776e+09 trial_f 1.59776e+09 accepted 1  

(pid=19004) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Repeated error test failures (internal error). Run with full_output = 1 to get quantitative information.
(pid=19004)   warnings.warn(warning_msg, ODEintWarning)


(pid=18401) warning: basinhopping: local minimization failure
(pid=18401) basinhopping step 9: f 1.58644e+09 trial_f 2.08693e+10 accepted 0  lowest_f 1.58644e+09
(pid=18406) basinhopping step 3: f 1.80904e+08 trial_f 1.85383e+08 accepted 0  lowest_f 1.80904e+08
(pid=18402) basinhopping step 9: f 1.43875e+08 trial_f 2.40757e+08 accepted 0  lowest_f 1.43875e+08
(pid=18403) basinhopping step 8: f 2.18158e+09 trial_f 2.70124e+09 accepted 0  lowest_f 2.18158e+09
(pid=18404) basinhopping step 4: f 191850 trial_f 191850 accepted 1  lowest_f 191850
(pid=18404) found new global minimum on step 4 with function value 191850
(pid=18407) basinhopping step 6: f 9.25607e+08 trial_f 9.55795e+08 accepted 0  lowest_f 9.25607e+08
(pid=19004) warning: basinhopping: local minimization failure
(pid=19004) basinhopping step 2: f 1.07559e+09 trial_f 1.50964e+09 accepted 0  lowest_f 1.07559e+09
(pid=18401) basinhopping step 10: f 1.58644e+09 trial_f 1.72109e+09 accepted 0  lowest_f 1.58644e+09
(pid=19004) basi

(pid=18407) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Repeated error test failures (internal error). Run with full_output = 1 to get quantitative information.
(pid=18407)   warnings.warn(warning_msg, ODEintWarning)


(pid=18406) basinhopping step 5: f 1.80904e+08 trial_f 1.86001e+08 accepted 0  lowest_f 1.80904e+08
(pid=19004) warning: basinhopping: local minimization failure
(pid=19004) basinhopping step 5: f 1.07559e+09 trial_f 1.07221e+11 accepted 0  lowest_f 1.07559e+09
(pid=18407)  lsoda--  at t(=r1) and step size h(=r2), the error  
(pid=18407)        test failed repeatedly or with abs(h) = hmin  
(pid=18407)       in above,  r1 =  0.2300640573652D+03   r2 =  0.1000000000000D-11
(pid=18407)  lsoda--  at t(=r1) and step size h(=r2), the error  
(pid=18407)        test failed repeatedly or with abs(h) = hmin  
(pid=18407)       in above,  r1 =  0.2194620676216D+03   r2 =  0.1000000000000D-11
(pid=18407)  lsoda--  at t(=r1) and step size h(=r2), the error  
(pid=18407)        test failed repeatedly or with abs(h) = hmin  
(pid=18407)       in above,  r1 =  0.2698038404162D+03   r2 =  0.1000000000000D-11
(pid=18407)  lsoda--  at t(=r1) and step size h(=r2), the error  
(pid=18407)        test fai

...

(pid=35590) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Repeated error test failures (internal error). Run with full_output = 1 to get quantitative information.
(pid=35590)   warnings.warn(warning_msg, ODEintWarning)


(pid=35590) warning: basinhopping: local minimization failure
(pid=35590) basinhopping step 1: f 3.47778e+07 trial_f 9.3777e+08 accepted 0  lowest_f 3.47778e+07
(pid=34647) warning: basinhopping: local minimization failure
(pid=34647) basinhopping step 7: f 7.11961e+08 trial_f 7.23625e+08 accepted 0  lowest_f 7.11961e+08
(pid=35590) warning: basinhopping: local minimization failure
(pid=35590) basinhopping step 2: f 3.47778e+07 trial_f 3.61354e+07 accepted 0  lowest_f 3.47778e+07
(pid=35590) warning: basinhopping: local minimization failure
(pid=35590) basinhopping step 3: f 3.47778e+07 trial_f 3.31282e+09 accepted 0  lowest_f 3.47778e+07
(pid=34647) warning: basinhopping: local minimization failure
(pid=34647) basinhopping step 8: f 7.11961e+08 trial_f 7.14664e+08 accepted 0  lowest_f 7.11961e+08
(pid=33623) warning: basinhopping: local minimization failure
(pid=33623) basinhopping step 6: f 1.17984e+08 trial_f 1.17984e+08 accepted 1  lowest_f 1.17984e+08
(pid=33623) found new global 

(pid=2336) /home/ats4i/anaconda3/envs/geo_env/lib/python3.6/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Repeated error test failures (internal error). Run with full_output = 1 to get quantitative information.
(pid=2336)   warnings.warn(warning_msg, ODEintWarning)


(pid=2336) warning: basinhopping: local minimization failure
(pid=2336) basinhopping step 6: f 5.39779e+07 trial_f 7.43909e+08 accepted 0  lowest_f 5.39779e+07
(pid=2336) basinhopping step 7: f 5.39779e+07 trial_f 5.67482e+07 accepted 0  lowest_f 5.39779e+07
(pid=2662) warning: basinhopping: local minimization failure
(pid=2662) basinhopping step 5: f 3.44032e+07 trial_f 5.67696e+09 accepted 0  lowest_f 3.44032e+07
(pid=2336) basinhopping step 8: f 5.39779e+07 trial_f 5.45821e+07 accepted 0  lowest_f 5.39779e+07
(pid=2662) warning: basinhopping: local minimization failure
(pid=2662) basinhopping step 6: f 3.44032e+07 trial_f 9.11571e+08 accepted 0  lowest_f 3.44032e+07
(pid=30723) warning: basinhopping: local minimization failure
(pid=30723) basinhopping step 7: f 4.57024e+08 trial_f 4.57024e+08 accepted 1  lowest_f 4.57024e+08
(pid=30723) found new global minimum on step 7 with function value 4.57024e+08
(pid=2294) basinhopping step 1: f 6.25757e+07 trial_f 6.25757e+07 accepted 1  low

(pid=4684) warning: basinhopping: local minimization failure
(pid=4684) basinhopping step 8: f 8.22187e+07 trial_f 3.24435e+09 accepted 0  lowest_f 8.22187e+07
(pid=5314) basinhopping step 2: f 7.61044e+08 trial_f 7.71053e+08 accepted 0  lowest_f 7.61044e+08
(pid=30723) warning: basinhopping: local minimization failure
(pid=30723) basinhopping step 10: f 4.57024e+08 trial_f 1.21239e+09 accepted 0  lowest_f 4.57024e+08
(pid=7456) basinhopping step 0: f 8.78571e+08
(pid=4684) warning: basinhopping: local minimization failure
(pid=4684) basinhopping step 9: f 6.73672e+07 trial_f 6.73672e+07 accepted 1  lowest_f 6.73672e+07
(pid=4684) found new global minimum on step 9 with function value 6.73672e+07
(pid=4000) warning: basinhopping: local minimization failure
(pid=4000) basinhopping step 1: f 8.06992e+07 trial_f 8.06992e+07 accepted 1  lowest_f 8.06992e+07
(pid=4000) found new global minimum on step 1 with function value 8.06992e+07
(pid=7456) warning: basinhopping: local minimization fai

In [ ]:
for i in range(0,len(DRS)):    

    districtRegion=DRS[i]
    query = dfparam.query('DRS == "{}"'.format(districtRegion)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")
    
    #s0, deltaDate, i0, d0, startNCases, weigthCases
    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "d0"] = optimal[i][3]
    dfparam.at[j, "START"] = optimal[i][4]
    dfparam.at[j, "WCASES"] = optimal[i][5]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    